In [ ]:
import torch
import torchvision

# Create a vector of zeros of size 5
size = (128, 128)
transform = torchvision.transforms.Compose([torchvision.transforms.Resize(size), torchvision.transforms.ToTensor()])
train_dataset = torchvision.datasets.Flowers102("/tmp/flowers", "train", transform=transform, download=True)
test_dataset = torchvision.datasets.Flowers102("/tmp/flowers", "test", transform=transform, download=True)

In [ ]:
class MyModel(torch.nn.Module):
    def __init__(self, layer_size=[512, 512, 512]):
        super().__init__()
        layers = []
        layers.append(torch.nn.Flatten())
        c = 128 * 128 * 3
        for s in layer_size:
            layers.append(torch.nn.Linear(c, s))
            layers.append(torch.nn.ReLU())
            c = s
        layers.append(torch.nn.Linear(c, 102))
        self.model = torch.nn.Sequential(*layers)

    def forward(self, x):
        return self.model(x)


train_loader = torch.utils.data.DataLoader(train_dataset, batch_size=64, shuffle=True)

model = MyModel(layer_size=[])
model.cuda()

loss_fn = torch.nn.CrossEntropyLoss()

optim = torch.optim.SGD(model.parameters(), lr=0.0001, momentum=0.9)

for epoch in range(10):
    for imgs, labels in train_loader:
        imgs, labels = imgs.cuda(), labels.cuda()
        pred = model(imgs)

        loss_val = loss_fn(pred, labels)

        optim.zero_grad()
        loss_val.backward()
        optim.step()
        print(loss_val.item())